# Lab 04: Data Science Tools

## 0. Jupyter Notebooks

Welcome to your first Jupyter notebook! Notebooks are made up of cells. Some cells contain text (like this one) and others contain Python code. 

Each cell can be in two different modes: editing or running. To edit a cell, double-click on it. When you're done editing, press **shift+Enter** to run it.  You can use [Markdown](https://www.markdownguide.org/cheat-sheet/) to add basic formatting to the text. Before you go on, try editing the text in this cell.

In [ ]:
# Other cells are code cells, containing Python code. (This is a comment, of course!)
# Try running this cell (again, shift+Enter). You'll see the result of the final statement 
# printed below the cell. 
# Then try changing the Python code and re-run it.

1+1

### 0.1 Cells share state

Even though code cells run one at a time, anything that happens in a cell (like declaring a variable or running a function) affects the whole notebook. Try running these two cells a few times, in different orders. What happens when you run *Cell B* over and over?

In [ ]:
# Cell A
x = 10
x

In [ ]:
# Cell B
x = x * 2
x

### 0.2 Saving your work

When you finish working on a notebook, save your work using the icon in the menu bar above. Your notebook is stored in the file `lab_04.ipynb` in the lab directory. You can commit your changes to `ipynb` files just like any other file. Once you finish with Jupyter, you can stop the server by pressing **Control + C** in the Terminal. 

---

## 1. Pandas

Pandas is probably the most important Python library for data science. Pandas provides an object called a **DataFrame**, which is basically a table with rows and columns. Most of the time, you will load data into Pandas using a `.csv` file. CSV files can be exported from Excel or Google Sheets, and are a common format for public data sets. 

In this lab, we'll be working with two data sets: The first contains Pokémon characteristics and the second comes from a wide-scale survey conducted by the US Centers for Disease Control ([details](https://www.cdc.gov/brfss/annual_data/annual_2020.html)). We will demonstrate techniques with Pokémon; your job is to replicate these tasks with the CDC dataset. 

**Note:** Pandas has *extensive* capabilities, and there's no way we could possibly present them all here. If you have a clearly-formed idea of what you want to do with tabular data, there's a way to do it. This lab introduces *some* of what Pandas can do, but expect to spend time reading the documentation and Stack Overflow when you start working on new tasks. 

### 1.0 Getting started

First, we'll import pandas (using the conventional variable name `pd`) and load the two datasets. *Run these cells and every code cell you encounter in this notebook.*

In [ ]:
import pandas as pd

In [ ]:
pokemon = pd.read_csv("pokemon.csv")
people = pd.read_csv("brfss_2020.csv")

### 1.1 A first look

#### Demo

Let's start by learning the *shape* of the data. How many columns are there? How many rows? What kinds of data are included?

In [ ]:
pokemon

OK, 800 Pokémon, with 12 columns for each. And you can see all the columns. Not all the data is shown in this preview, of course. If there were more columns than could be displayed, you could see them all by typing `pokemon.columns`. 

#### Your turn

Now do the same for your data set, `people`.

In [ ]:
# Your code here

### 1.2 Descriptive Statistics

#### Demo

Let's get a sense of the data contained in some of the columns. For categorical data like `generation`, it makes sense to look at value counts--showing us how many of each category there are. You can use the optional keyword `normalize=True` to see percentage of total instead of frequencies. 

In [ ]:
pokemon.generation.value_counts()

For numeric data, we could start by looking at the mean value. We can select multiple columns and get all the column means at once.

In [ ]:
pokemon[["hp", "attack", "defense", "speed"]].mean()

We can also compute the mean of boolean data. In this case, True will map to 1 and False will map to 0. So the mean value equals the percentage of data which is True. 

In [ ]:
pokemon.legendary.mean()

Just over 8% of Pokemon are legendary.

#### Your turn

**1.2.0.** In this survey, people are grouped into age bands of 18-24, 25-34, 35-44, 45-54, 55-64, and 65+, with the lower bound reported. What percentage of people are in each age band? (When we talk about "people" in this lab, we're referring to the people who responded to the survey, not the whole US population.)

In [ ]:
# Your code here

**1.2.1.** What are the mean height and weight of people in this survey?

In [ ]:
# Your code here

**1.2.2.** The `exercise` column indicates whether a person has done any physical activity or exercise in the last 30 days, outside of work. What percentage of people have done exercise?

In [ ]:
# Your code here

### 1.3 Filtering

Sometimes we're just interested in a selection of the data set. The way to do this is to create a boolean series, and then use this to select which rows you want to include. Vocabulary note: A dataframe is two-dimensional, with rows and columns. A series (a single row or a single column) is one-dimensional. 

#### Demo
`pokemon.legendary` is already boolean, so we can use this to select just the legendary pokémon. 

In [ ]:
legendary = pokemon[pokemon.legendary]
legendary

Let's get all the ice pokémon. We can create a boolean series from another series...

In [ ]:
pokemon.type == "Ice"

And then use this series to select just the ice pokémon. 

In [ ]:
ice = pokemon[pokemon.type == "Ice"]
ice

Let's get the high-speed ice pokémon. You can join conditions together using the `&` (and) and `|` (or) operators. `~` means "not", so `pokemon[~(pokemon.type == "Ice")]` would select all the non-ice pokémon. Due to order of operations, each condition needs to be wrapped in parentheses.

In [ ]:
high_speed_ice = pokemon[(pokemon.type == "Ice") & (pokemon.speed >= 80)]
high_speed_ice

You could get the pokémon who are fire or ice by selecting `pokemon[(pokemon.type == "Fire") | (pokemon.type == "Ice")]`.

#### Your turn

**1.3.0.** `no_doctor` indicates whether there was a time in the last year when the person needed to see a doctor, but could not afford to do so. Create a dataframe containing only these people. 

In [ ]:
# YOUR CODE HERE

**1.3.1.** `health` asks people for their general health, with the meanings of numbers shown below. Create a dataframe which contains people whose general health is good or better. 

| number | health status | 
| ------ | ----------- |
| 1      | Poor        |
| 2      | Fair        |
| 3      | Good        |
| 4      | Very good   |
| 5      | Excellent   |

In [ ]:
# YOUR CODE HERE

**1.3.2.**. `education` indicates the highest level of education completed, with codes as follows. Create a dataframe which only contains female college graduates who needed a doctor but couldn't afford one. (The survey asked people for their current sex, and only had options for male and female.)

| number | education level      | 
| ------ | ----------- |
| 1      | Did not graduate from high school        |
| 2      | Graduated from high school        |
| 3      | Attended some college        |
| 4      | Graduated from college   |

In [ ]:
# YOUR CODE HERE

### 1.4. Grouping

Now things get crazy. You can group a dataframe using one or more columns, and then compare their statistics. 

#### Demo

Do different types of pokémon move at different speeds? We'll use `sort_values` to put these in order from slow to fast.

In [ ]:
pokemon.groupby("type").speed.mean().sort_values()

Do types differ in other stats? Let's sort by hit points. 

In [ ]:
ptypes = pokemon.groupby("type")
ptypes[["hp", "attack", "defense"]].mean().sort_values("hp")

Which type/subtype combinations are most likely to have legendary pokémon?

In [ ]:
legendary_percentages = pokemon.groupby(["type", "subtype"]).legendary.mean().sort_values() 
legendary_percentages[legendary_percentages > 0.5]

#### Your turn

**1.4.0.** `income` records peoples' annual income, in the following bands. `sleep` records the average hours of sleep someone gets per night. Is there a difference in the average hours of sleep by income level?

| number | annual income, in $1000   | 
| ------ | ----------- |
| 1      | Less than 10       |
| 2      | 10-15        |
| 3      | 15-20         |
| 4      | 20-25        |
| 5      | 25-35        |
| 6      | 35-50        |
| 7      | 50-75        |
| 8      | More than 75   |

In [ ]:
# YOUR CODE HERE

**1.4.0.** Is there a difference in peoples' income or general health, by sex and education level? 

In [ ]:
# YOUR CODE HERE

### 1.5. Plotting 

Pandas has excellent built-in plotting capabilities, but 
we are going to use the [seaborn](https://seaborn.pydata.org/) library because it's a bit 
more intuitive and produces more beautiful plots. `set_theme`, called here without any arguments, assigns the default color palette. 

In [ ]:
import seaborn as sns
sns.set_theme()

#### Demo

**When you want to visualize the distribution of a series**, a [histogram](https://seaborn.pydata.org/generated/seaborn.histplot.html) puts data into bins and plots the number of data points in each bin.

Let's see the distribution of pokémon attack values. Note how assigning `x="attack"` spreads attack values over the x-axis, while `y="attack"` spreads attack values over the y-axis. The number of bins is selected automatically, but you can specify this with the optional `bins` argument. 

In [ ]:
sns.histplot(data=pokemon, x="attack")

In [ ]:
sns.histplot(data=pokemon, y="attack", bins=5)

**When you want to compare the distribution of a numeric variable across categories**, a [barplot](https://seaborn.pydata.org/generated/seaborn.barplot.html) is a good choice. Choose one numeric column and one categorical column. 

Let's see pokémon hit points by legendary/non-legendary. `ci="sd"` shows the standard deviation for each category. 

In [ ]:
sns.barplot(data=pokemon, x="legendary", y="hp", ci="sd")

Here, we use a barplot to show average hit points by type. `ci=None` removes the standard deviation bars, because they clutter up the plot with too much detail. 

In [ ]:
sns.barplot(data=pokemon, x="hp", y="type", ci=None, palette="muted")

**When you want to show how many observations are the intersection of multiple categories,** a [countplot](https://seaborn.pydata.org/generated/seaborn.countplot.html) is a good choice. 

To demonstrate this, let's convert the numeric variable `speed` into a categorical variable, `speed_category`, using the built-in function [cut](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.cut.html). 

In [ ]:
bins = [0, 50, 100, 200]
labels = ["slow", "medium", "fast"]
pokemon["speed_category"] = pd.cut(pokemon.speed, bins=bins, labels=labels)

In [ ]:
sns.countplot(data=pokemon, x="speed_category", hue="legendary")

**When you want to show the relationship between two numeric variables**, a [scatterplot](https://seaborn.pydata.org/generated/seaborn.scatterplot.html) is a good choice. 

Here, we plot pokémon hit points against their speed. 

In [ ]:
sns.scatterplot(data=pokemon, x="hp", y="speed")

You can distinguish between categories within a scatter plot by assigning a categorical variable to `hue`. We set the marker size with `s` and their opacity with `alpha`. 

In [ ]:
sns.scatterplot(data=pokemon, x="hp", y="speed", hue="legendary", alpha=0.5, s=60)

Finally, if you want scatter plots across multiple categories, a [relplot](https://seaborn.pydata.org/generated/seaborn.relplot.html) lets you distribute categories across rows and colums in a grid. 

In [ ]:
favorite_types = pokemon[pokemon.type.isin(["Fire", "Water", "Grass"])]
sns.relplot(data=favorite_types, x="hp", y="speed", hue="legendary", col="type", s=100)

#### Your turn

**1.5.0.** Plot a histogram of peoples' heights.

In [ ]:
# Your code here

**1.5.1.** Plot a bar chart showing peoples' average hours of sleep by age. 

In [ ]:
# Your code here

**1.5.2.** Plot a bar chart showing peoples' likelihood of getting exercise by income. 

In [ ]:
# Your code here

**1.5.3.** Plot a bar chart showing average reported health by age. For each age, show average health for those who get exercise and those who don't.

In [ ]:
# Your code here

**1.5.4.** Create a plot showing the number of people at each income level, for each education level. 

In [ ]:
# Your code here

**1.5.5.** Plot side-by-side scatter plots showing the relationship between height and weight for males and females. (There are so many overlapping dots that the plot will be more informative if you lower the opacity of each dot. Try using `alpha=0.1` and `edgecolor=None`.)

In [ ]:
# Your code here

## 2. Crafting a data argument

Everything up to here are just tools, worthless without a clear research question and a convincing argument. Choose a research question that interests you which might be answerable using the `people` dataset. Then do your best to find the answer in the space below. This answer should include data analysis (code cells) as well as written argument (text cells) explaining what the data means and why you believe it answers your question. 

Examples of research questions might include:

- Do older people tend to have higher incomes?
- Do people who sleep at least 6 hours a night tend to report better health? 
- Is it more common for males to be bisexual than females?

**A note of caution:** this lab has given you tools for exploring associations--patterns that tend to co-occur. These tools *do not* equip you to argue that one variable causes another to change. For example: Plot 1.5.4 showed that people who are taller also tend to be heaver, with a lot of individual variation. But are people heavier *because* they are taller? Are they taller because they are heavier? Or maybe neither variable causes the other--perhaps they're both caused by something else. If you want to be able to answer questions like these, take a course on statistics.

In [ ]:
# Your code here. Feel free to add new text cells and code cells as necessary.